In [1]:

import os
import boto3
import pandas as pd

import csv

from geopy.geocoders import Nominatim
import folium
from folium.plugins import MarkerCluster

from pathlib import Path

from botocore import UNSIGNED
from botocore.client import Config


In [2]:

#Função que permite descarregar todos os ficheiros de uma pasta contida no bucket pretendido

def download_all_objects_in_folder(s3_resource, bucket_name, prefix):
    
    # seleção do bucket
    my_bucket = s3_resource.Bucket(bucket_name)
    
    objects = my_bucket.objects.filter(Prefix=prefix)
    for obj in objects:
        path, filename = os.path.split(obj.key)
        my_bucket.download_file(obj.key, filename)


In [3]:

#Inicialização do resource s3
s3_resource = boto3.resource('s3', config=Config(signature_version=UNSIGNED))


In [4]:

#Chamada da função de modo a descarregar os ficheiros parquet que contêm os dados obtidos na plataforma AWS
#download_all_objects_in_folder(s3_resource,"bigdatanoaa","world_map")

#Diretoria de trabalho pertencente à virtual machine
data_dir = Path('/home/big/Desktop/Trabalho')

#São agregados todos os dados que estejam contidos em ficheiros parquet
full_df = pd.concat(
    pd.read_parquet(parquet_file)
    for parquet_file in data_dir.glob('*.parquet')
)

#Conversão dos dados obtidos anteriormente para o formato csv
full_df.to_csv('data.csv')

#Criação de um pandas dataframe com os dados pretendidos
predict = pd.read_csv('data.csv')


In [5]:

#Chamada do mapa do mundo

world_map = folium.Map()
geolocator = Nominatim(user_agent="Temperatures")

#Array de cores usado no preenchimento dos diversos clusters
city_color = [
    "red",
    "yellow",
    "blue",
    "yellow",
    "violet",
    "purple",
    "pink",
    "silver",
    "gold",
    "green",
    "brown",
    "black",
    "gray",
]

#Os dados serão percorridos linha a linha, com o objetivo de adicionarmos ao mapa todas as estações do hemisfério norte
for index,raw in predict.iterrows():

    lat = raw["LATITUDE"] 
    long = raw["LONGITUDE"]

    folium.Circle(location=[lat, long],
                popup=raw["NOME"],
                radius=30000,
                color=city_color[raw["prediction"]],
                fill=True,
                fill_color=city_color[raw["prediction"]]).add_to(world_map)

#Visualização do mapa do mundo preenchido com os clusters relativos às diversas estações meteorológicas
world_map